# Analyze the Pluvio Data - Entire Season + Case Selection

## Imports

In [23]:
import act
import glob
import xarray as xr
import hvplot.xarray
import holoviews as hv
hv.extension("bokeh")

## Data Access

In [7]:

files = act.discovery.download_arm_data(
    "mgrover4", "176e1559b67be630", "gucwbpluvio2M1.a1", "2021-12-01", "2022-03-31"
)

[DOWNLOADING] gucwbpluvio2M1.a1.20220317.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220318.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220319.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220320.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220321.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220322.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220323.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220324.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220325.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220326.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220327.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220328.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220329.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220330.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220331.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20220224.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20211201.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20211202.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1.20211203.000000.nc
[DOWNLOADING] gucwbpluvio2M1.a1

## Load Data into Xarray and Compute Accumulation Using ACT

In [10]:
files = sorted(glob.glob("gucwbpluvio2M1.a1/*"))

In [29]:
ds = xr.open_mfdataset(files, engine='netcdf4')

In [30]:
gauge_precip_accum = act.utils.accumulate_precip(ds.where(ds.pluvio_status == 0), "intensity_rtnrt").intensity_rtnrt_accumulated.compute()

## Visualize our Data

### Entire Season

In [31]:
ds.intensity_rtnrt.hvplot(width=300, height=200) * gauge_precip_accum.hvplot(width=300, height=200)

:Overlay
   .Curve.I  :Curve   [time]   (intensity_rtnrt)
   .Curve.II :Curve   [time]   (intensity_rtnrt_accumulated)

In [34]:
ds.sel(time=slice("2021-12-23", "2022-01-01")).intensity_rtnrt.hvplot(width=300, height=200) * gauge_precip_accum.sel(time=slice("2021-12-23", "2022-01-01")).hvplot(width=300, height=200)

:Overlay
   .Curve.I  :Curve   [time]   (intensity_rtnrt)
   .Curve.II :Curve   [time]   (intensity_rtnrt_accumulated)

In [37]:
ds.sel(time=slice("2022-03-04", "2022-03-07")).intensity_rtnrt.hvplot(width=300, height=200) * gauge_precip_accum.sel(time=slice("2022-03-04", "2022-03-07")).hvplot(width=300, height=200)

:Overlay
   .Curve.I  :Curve   [time]   (intensity_rtnrt)
   .Curve.II :Curve   [time]   (intensity_rtnrt_accumulated)

## Compare with the Gothic Site

In [46]:
import pandas as pd
from metpy.units import units

In [ ]:
"https://docs.google.com/spreadsheets/d/1S7xZPT0IoJk0bWt34BKvyT9xzPbI1Tv6q28M3ZqiMpE/edit?usp=sharing"

In [90]:
df = pd.read_excel('https://docs.google.com/spreadsheets/d/' + 
                   '1S7xZPT0IoJk0bWt34BKvyT9xzPbI1Tv6q28M3ZqiMpE' +
                   '/export?gid=0&format=xlsx',
                   sheet_name='Sheet1')
df

Date temp ºC (ºF) cm (inches)  Snow accumulation (cm)  \
0   2021-12-01     -7½ (18)    11½ (53)                     0.0   
1   2021-12-02      -8 (18)    12½ (55)                     0.0   
2   2021-12-03     -8½ (17)    11½ (53)                     0.0   
3   2021-12-04     -8½ (17)     9½ (49)                     0.0   
4   2021-12-05      -8 (18)     5½ (42)                     0.0   
..         ...          ...         ...                     ...   
178 2022-05-29      -½ (31)    13½ (56)                     0.0   
179 2022-05-30     -2½ (27)     5½ (42)                     9.0   
180 2022-05-31     -5½ (22)     11 (52)                     2.0   
181        NaT          NaN         NaN                     NaN   
182        NaT          NaN         NaN                     NaN   

     Liquid equivalent (in) Accumulation Ratio  
0                       0.0            #DIV/0!  
1                       0.0            #DIV/0!  
2                       0.0            #DIV/0!  
3                       0.0            #DIV/0!  
4                       0.0            #DIV/0!  
..                      ...                ...  
178                     0.0            #DIV/0!  
179                     0.5           7.086614  
180                     0.1           7.874016  
181                     NaN                NaN  
182                     NaN            #DIV/0!  

[183 rows x 6 columns]

### Convert all units to millimeters and set the date column as the index

In [91]:
# Add units
swe_inches = df["Liquid equivalent (in)"].astype(float).values * units.inches
accum_cm = df["Snow accumulation (cm)"].astype(float).values * units.centimeter

# Do the conversion using MetPy
swe_mm = swe_inches.to("mm")
accum_mm = accum_cm.to("mm")

# Strip Units
df["swe_mm"] = swe_mm.m
df["accum_mm"] = accum_mm.m

# Set the index to date
df["Date"] = pd.to_datetime(df.Date)
df = df.set_index("Date")

# Convert to xarray!
gothic_ds = df.to_xarray().dropna("Date")

### Visualize the Gothic Colorado Snow Accumulation and Snow Water Liquid Equivalent (SWE)

In [92]:
(gothic_ds["swe_mm"].hvplot(width=400,
                            title='Snow water liquid equivalent (SWE) at Gothic') + 
 gothic_ds["accum_mm"].hvplot(width=400,
                              title='Snow depth at Gothic')
).cols(1)

:Layout
   .Curve.I  :Curve   [Date]   (swe_mm)
   .Curve.II :Curve   [Date]   (accum_mm)